In [9]:
import numpy as np
import pandas as pd
from pathlib import Path
import re

In [10]:
# define some needed variables, lists, and the like
events = {'wmpo': 't003', 'api': 't009', 'tpc': 'to11', 'rbch': 't012', 'masters': 't014', 'pga': 't033'}
stats = {'drv': '101', 'gir': '103', 't2g': '02674', 'scramble': '130'}
st_cols = {'drv': ['PLAYER NAME', 'AVG.', 'TOTAL DISTANCE', 'TOTAL DRIVES'],
           'gir': ['PLAYER NAME', '%', 'GREENS HIT', '# HOLES', 'RELATIVE/PAR'],
           't2g': ['PLAYER NAME', 'AVERAGE', 'SG:OTT', 'SG:APR', 'SG:ARG'],
           'scramble': ['PLAYER NAME', '%', 'PAR OR BETTER', 'MISSED GIR']
}
# data directory and stats, tournaments and years to process
d_dir = "./data/"
p_sids = ['drv', 'gir']
p_tids = ['pga', 'rbch']
p_yrs = ['2020', '2021']

In [11]:
# function: take year, tounament id and stat id, return CSV file path (relative) 
def get_csv_nm(t_yr, t_id, p_st):
    global d_dir
    return f"{d_dir}{t_id}_{t_yr}_{p_st}_2.test.csv"

# function: will take a year, tournament and stat, read csv, return suitable DataFrame
def csv_2_df(t_yr, t_id, p_st):
    """ Read appropriate CSV file into DataFrame. Modify Dataframe to employ multi-indices.
        Return modified DataFrame.
        Useage: csv_2_df(t_yr, t_id, p_st)
          where t_yr = tournament year
                t_id = tournament id (e.g. 'pga')
                p_st = player stat (e.g. 'drv', 'gir')
    """
    global st_cols
    col_nms = {'drv': {'AVG.': 'drv'},
                'gir': {'%': 'gir'},
                'scramble': {'%': 'scramble'}
    }

    csv_fl = get_csv_nm(t_yr, t_id, p_st)
    ty_m_idx = pd.MultiIndex.from_tuples([(t_yr, t_id)])
    s_col = st_cols[p_st][1]
    df_stats = pd.read_csv(csv_fl, index_col=['PLAYER NAME'], usecols=[s_col, 'PLAYER NAME'])
    df_stats.rename(columns=col_nms[p_st], inplace=True)
    s_tmp = df_stats.stack()
    ts_df = pd.DataFrame(s_tmp, columns=ty_m_idx)
    ts_df.rename_axis(['player', 'stat'], inplace=True)
    return ts_df

In [12]:
# quick test
df1 = csv_2_df('2020', 'pga', 'drv')
display(df1)
df2 = csv_2_df('2020', 'pga', 'gir')
display(df2)

2020
                          pga
player            stat       
Cameron Champ     drv   321.1
Bryson DeChambeau drv   318.1
Rory McIlroy      drv   312.5
Sepp Straka       drv   305.8
Tommy Fleetwood   drv   305.5
...                       ...
Charl Schwartzel  drv   276.0
Chez Reavie       drv   274.5
Brendon Todd      drv   272.3
Patrick Reed      drv   271.6
Mark Hubbard      drv   268.8

[79 rows x 1 columns]

2020
                         pga
player           stat       
Matthew Wolff    gir   77.78
Paul Casey       gir   76.39
Jason Day        gir   76.39
Louis Oosthuizen gir   73.61
Cameron Champ    gir   73.61
...                      ...
Denny McCarthy   gir   54.17
Harris English   gir   52.78
Brian Harman     gir   51.39
Brandt Snedeker  gir   51.39
J.T. Poston      gir   50.00

[79 rows x 1 columns]

In [13]:

# function: will take a year, a tournament and a list of stats, generate a DataFrame for that tournament and year
def tourney_2_df(t_yr, t_id, p_sts):
    """ Combine all requested stats for a given tournament and year into a single DataFrame. 
        Return DataFrame.
        Useage: tourney_2_df(t_yr, t_id, p_sts)
          where t_yr = tournament year
                t_id = tournament id (e.g. 'pga')
                p_sts = list of player stat (e.g. ['drv', 'gir'])
    """
    df1 = csv_2_df(t_yr, t_id, p_sts[0])
    if len(p_sts) > 1:
        df2 = csv_2_df(t_yr, t_id, p_sts[1])
        df_tourney = pd.concat([df1, df2])
    else:
        return df1
    if len(p_sts) > 2:
        passs
    
    ndx_sort2 = sorted(df_tourney.index,key=lambda x: re.split(r'\W+', x[0])[-1])
    df_tourney = df_tourney.reindex(ndx_sort2)
    return df_tourney


In [14]:
# test
pga_2020 = tourney_2_df('2020', 'pga', ['drv', 'gir'])
display(pga_2020)

2020
                       pga
player        stat        
Byeong Hun An drv   286.60
              gir    62.50
Abraham Ancer drv   295.60
              gir    63.89
Daniel Berger drv   291.90
...                    ...
Matthew Wolff gir    77.78
Gary Woodland drv   293.00
              gir    65.28
Tiger Woods   drv   304.00
              gir    62.50

[158 rows x 1 columns]

In [15]:
# function: will take a year, list of tournaments and list of stats and generate a DataFrame for that year
def year_2_df(t_yr, t_ids, p_sts):
    df1 = tourney_2_df(t_yr, t_ids[0], p_sts)
    if len(t_ids) == 1:
        return df1
    df2 = tourney_2_df(t_yr, t_ids[1], p_sts)
    df_comb = pd.merge(df1, df2, how='outer', on=['player', 'stat'])
    if len(t_ids) > 2:
        pass
    ndx_sort2 = sorted(df_comb.index,key=lambda x: re.split(r'\W+', x[0])[-1])
    df_comb = df_comb.reindex(ndx_sort2)

    return df_comb

In [32]:
# test year_2_df
df_2020 = year_2_df('2020', ['pga', 'rbch'], ['drv', 'gir'])
display(df_2020)
# want to see what the csv looks like
golf_csv = f'{d_dir}golf_play_8.test.csv'
df_2020.to_csv(golf_csv)

2020        
                       pga    rbch
player        stat                
Byeong Hun An drv   286.60     NaN
              gir    62.50     NaN
Abraham Ancer drv   295.60  278.10
              gir    63.89   90.28
Ryan Armour   drv      NaN  275.00
...                    ...     ...
Matthew Wolff gir    77.78     NaN
Gary Woodland drv   293.00  287.00
              gir    65.28   73.61
Tiger Woods   drv   304.00     NaN
              gir    62.50     NaN

[234 rows x 2 columns]

In [17]:
# test merging two years
df_2021 = year_2_df('2021', ['pga', 'rbch'], ['drv', 'gir'])
display(df_2021)
df_comb = pd.merge(df_2020, df_2021, how='outer', on=['player', 'stat'])
ndx_sort2 = sorted(df_comb.index,key=lambda x: re.split(r'\W+', x[0])[-1])
df_comb = df_comb.reindex(ndx_sort2)
display(df_comb)

2021        
                        pga    rbch
player         stat                
Byeong Hun An  drv   306.50     NaN
               gir    48.61     NaN
Abraham Ancer  drv   301.80  299.90
               gir    61.11   70.83
Daniel Berger  drv   298.40  299.60
...                     ...     ...
Aaron Wise     gir    54.17     NaN
Gary Woodland  drv   311.10     NaN
               gir    58.33     NaN
Will Zalatoris drv   306.50  312.00
               gir    61.11   58.33

[226 rows x 2 columns]

2020            2021        
                        pga    rbch     pga    rbch
player         stat                                
Byeong Hun An  drv   286.60     NaN  306.50     NaN
               gir    62.50     NaN   48.61     NaN
Abraham Ancer  drv   295.60  278.10  301.80  299.90
               gir    63.89   90.28   61.11   70.83
Ryan Armour    drv      NaN  275.00     NaN     NaN
...                     ...     ...     ...     ...
Gary Woodland  gir    65.28   73.61   58.33     NaN
Tiger Woods    drv   304.00     NaN     NaN     NaN
               gir    62.50     NaN     NaN     NaN
Will Zalatoris drv      NaN     NaN  306.50  312.00
               gir      NaN     NaN   61.11   58.33

[318 rows x 4 columns]

In [18]:
# let's try that with 3 different stats
# will need to redefine tourney_2_df
# you may have noticed the extra condition with only a 'pass'
def tourney_2_df(t_yr, t_id, p_sts):
    """ Combine all requested stats for a given tournament and year into a single DataFrame. 
        Return DataFrame.
        Useage: tourney_2_df(t_yr, t_id, p_sts)
          where t_yr = tournament year
                t_id = tournament id (e.g. 'pga')
                p_sts = list of player stat (e.g. ['drv', 'gir'])
    """
    df1 = csv_2_df(t_yr, t_id, p_sts[0])
    if len(p_sts) > 1:
        df2 = csv_2_df(t_yr, t_id, p_sts[1])
        df_tourney = pd.concat([df1, df2])
    else:
        return df1
    if len(p_sts) > 2:
        all_dfs = [df_tourney]
        for p_st in p_sts[2:]:
            df_tmp = csv_2_df(t_yr, t_id, p_st)
            all_dfs.append(df_tmp)
        df_tourney = pd.concat(all_dfs)
    
    ndx_sort2 = sorted(df_tourney.index,key=lambda x: re.split(r'\W+', x[0])[-1])
    df_tourney = df_tourney.reindex(ndx_sort2)
    return df_tourney

In [19]:
# test time
p_sts = ['drv', 'gir', 'scramble']
pga_2020 = tourney_2_df('2020', 'pga', p_sts)
display(pga_2020)

2020
                           pga
player        stat            
Byeong Hun An drv       286.60
              gir        62.50
              scramble   62.96
Abraham Ancer drv       295.60
              gir        63.89
...                        ...
Gary Woodland gir        65.28
              scramble   64.00
Tiger Woods   drv       304.00
              gir        62.50
              scramble   59.26

[237 rows x 1 columns]

In [31]:
# that seemed to work, so let's do a second tourney and merge
df_2020 = year_2_df('2020', ['pga', 'rbch'], ['drv', 'gir', 'scramble'])
display(df_2020)

2020        
                           pga    rbch
player        stat                    
Byeong Hun An drv       286.60     NaN
              gir        62.50     NaN
              scramble   62.96     NaN
Abraham Ancer drv       295.60  278.10
              gir        63.89   90.28
...                        ...     ...
Gary Woodland gir        65.28   73.61
              scramble   64.00   42.11
Tiger Woods   drv       304.00     NaN
              gir        62.50     NaN
              scramble   59.26     NaN

[351 rows x 2 columns]

In [21]:
# okay, and now a 2nd year
df_2021 = year_2_df('2021', ['pga', 'rbch'], ['drv', 'gir', 'scramble'])
display(df_2021)
df_comb = pd.merge(df_2020, df_2021, how='outer', on=['player', 'stat'])
ndx_sort2 = sorted(df_comb.index,key=lambda x: re.split(r'\W+', x[0])[-1])
df_comb = df_comb.reindex(ndx_sort2)
display(df_comb)

2021        
                            pga    rbch
player         stat                    
Byeong Hun An  drv       306.50     NaN
               gir        48.61     NaN
               scramble   67.57     NaN
Abraham Ancer  drv       301.80  299.90
               gir        61.11   70.83
...                         ...     ...
Gary Woodland  gir        58.33     NaN
               scramble   60.00     NaN
Will Zalatoris drv       306.50  312.00
               gir        61.11   58.33
               scramble   64.29   56.67

[339 rows x 2 columns]

2020            2021        
                            pga    rbch     pga    rbch
player         stat                                    
Byeong Hun An  drv       286.60     NaN  306.50     NaN
               gir        62.50     NaN   48.61     NaN
               scramble   62.96     NaN   67.57     NaN
Abraham Ancer  drv       295.60  278.10  301.80  299.90
               gir        63.89   90.28   61.11   70.83
...                         ...     ...     ...     ...
Tiger Woods    gir        62.50     NaN     NaN     NaN
               scramble   59.26     NaN     NaN     NaN
Will Zalatoris drv          NaN     NaN  306.50  312.00
               gir          NaN     NaN   61.11   58.33
               scramble     NaN     NaN   64.29   56.67

[477 rows x 4 columns]

In [22]:
# now let's add a 3rd tournament
# and of course we need to redefine year_2_df
def year_2_df(t_yr, t_ids, p_sts):
    df1 = tourney_2_df(t_yr, t_ids[0], p_sts)
    if len(t_ids) == 1:
        return df1
    df2 = tourney_2_df(t_yr, t_ids[1], p_sts)
    df_comb = pd.merge(df1, df2, how='outer', on=['player', 'stat'])
    if len(t_ids) > 2:
        for t_id in t_ids[2:]:
            df_tmp = tourney_2_df(t_yr, t_id, p_sts)
            df_comb = pd.merge(df_comb, df_tmp, how='outer', on=['player', 'stat'])

    ndx_sort2 = sorted(df_comb.index,key=lambda x: re.split(r'\W+', x[0])[-1])
    df_comb = df_comb.reindex(ndx_sort2)

    return df_comb

In [23]:
# testing 1 2 3
df_2020 = year_2_df('2020', ['api', 'pga', 'rbch'], ['drv', 'gir', 'scramble'])
display(df_2020)


2020                
                           api     pga    rbch
player        stat                            
Byeong Hun An drv       291.80  286.60     NaN
              gir        66.67   62.50     NaN
              scramble   54.17   62.96     NaN
Abraham Ancer drv       281.90  295.60  278.10
              gir        48.61   63.89   90.28
...                        ...     ...     ...
Tiger Woods   gir          NaN   62.50     NaN
              scramble     NaN   59.26     NaN
Xinjun Zhang  drv       288.80     NaN     NaN
              gir        50.00     NaN     NaN
              scramble   52.78     NaN     NaN

[441 rows x 3 columns]

In [24]:
# add the second year
df_2021 = year_2_df('2021', ['api', 'pga', 'rbch'], ['drv', 'gir', 'scramble'])
df_comb = pd.merge(df_2020, df_2021, how='outer', on=['player', 'stat'])
ndx_sort2 = sorted(df_comb.index,key=lambda x: re.split(r'\W+', x[0])[-1])
df_comb = df_comb.reindex(ndx_sort2)
display(df_comb)

2020                    2021                
                            api     pga    rbch     api     pga    rbch
player         stat                                                    
Byeong Hun An  drv       291.80  286.60     NaN  290.60  306.50     NaN
               gir        66.67   62.50     NaN   56.94   48.61     NaN
               scramble   54.17   62.96     NaN   64.52   67.57     NaN
Abraham Ancer  drv       281.90  295.60  278.10     NaN  301.80  299.90
               gir        48.61   63.89   90.28     NaN   61.11   70.83
...                         ...     ...     ...     ...     ...     ...
Will Zalatoris gir          NaN     NaN     NaN   69.44   61.11   58.33
               scramble     NaN     NaN     NaN   59.09   64.29   56.67
Xinjun Zhang   drv       288.80     NaN     NaN     NaN     NaN     NaN
               gir        50.00     NaN     NaN     NaN     NaN     NaN
               scramble   52.78     NaN     NaN     NaN     NaN     NaN

[558 rows x 6 columns]

In [25]:
# decided to test using an additional year, 2019
# so need to get some more stats into csv files
def stats_2_csv(tyrs, tids, psts):
    global d_dir, events, stats, st_cols
    for tid in tids:
        eid = events[tid]
        for tyr in tyrs:
            for pst in psts:
                print(f"\n{tid}, {tyr}, {pst} ->", end='')
                stid = stats[pst]
                tlnk = f'https://www.pgatour.com/content/pgatour/stats/stat.{stid}.y{tyr}.eon.{eid}.html'
                f_out = get_csv_nm(tyr, tid, pst)
                if Path(f_out).is_file():
                    print(" already exists, not downloaded again")
                else:
                    tmp_stats = pd.read_html(tlnk)
                    if len(tmp_stats) <= 1:
                        print(" not found on site")
                        break
                    df_stats = tmp_stats[1][st_cols[pst]]
                    df_stats.to_csv(f_out, index=False)
                    print(" downloaded and saved to CSV")

In [26]:
p_sts = ['drv', 'gir', 'scramble']
t_ids = ['api', 'pga', 'rbch']
t_yrs = ['2019']
stats_2_csv(t_yrs, t_ids, p_sts)


api, 2019, drv -> already exists, not downloaded again

api, 2019, gir -> already exists, not downloaded again

api, 2019, scramble -> already exists, not downloaded again

pga, 2019, drv -> already exists, not downloaded again

pga, 2019, gir -> already exists, not downloaded again

pga, 2019, scramble -> already exists, not downloaded again

rbch, 2019, drv -> already exists, not downloaded again

rbch, 2019, gir -> already exists, not downloaded again

rbch, 2019, scramble -> already exists, not downloaded again


In [27]:
# now a new function to build the final df by combining the ones for each year
def golf_stats_2_df(tyrs, tids, psts):
    if len(tyrs) < 1:
        return None
    else:    
        df1 = year_2_df(tyrs[0], tids, psts)
        if len(tyrs) == 1:
            return df1
        else:
            df2 = year_2_df(tyrs[1], tids, psts)
            df_comb = pd.merge(df1, df2, how='outer', on=['player', 'stat'])
            if len(tyrs) > 2:
                for tyr in tyrs[2:]:
                    df_tmp = year_2_df(tyr, tids, psts)
                    df_comb = pd.merge(df_comb, df_tmp, how='outer', on=['player', 'stat'])

        ndx_sort2 = sorted(df_comb.index,key=lambda x: re.split(r'\W+', x[0])[-1])
        df_comb = df_comb.reindex(ndx_sort2)

        return df_comb

In [28]:
# test time
# manually edidted the appropriate csv files and removed the ', Jr.' for the Ted Potter row
all_yrs = ['2019', '2020', '2021']
golf_stats = golf_stats_2_df(all_yrs, t_ids, p_sts)
display(golf_stats)
# want to see what the csv looks like
golf_csv = f'{d_dir}golf_stats.test.csv'
golf_stats.to_csv(golf_csv)

2019                 2020                    2021  \
                            api     pga rbch     api     pga    rbch     api   
player         stat                                                            
Byeong Hun An  drv       312.90     NaN  NaN  291.80  286.60     NaN  290.60   
               gir        63.89     NaN  NaN   66.67   62.50     NaN   56.94   
               scramble   69.23     NaN  NaN   54.17   62.96     NaN   64.52   
Abraham Ancer  drv          NaN  285.60  NaN  281.90  295.60  278.10     NaN   
               gir          NaN   56.94  NaN   48.61   63.89   90.28     NaN   
...                         ...     ...  ...     ...     ...     ...     ...   
Will Zalatoris gir          NaN     NaN  NaN     NaN     NaN     NaN   69.44   
               scramble     NaN     NaN  NaN     NaN     NaN     NaN   59.09   
Xinjun Zhang   drv          NaN     NaN  NaN  288.80     NaN     NaN     NaN   
               gir          NaN     NaN  NaN   50.00     NaN     NaN     NaN   
               scramble     NaN     NaN  NaN   52.78     NaN     NaN     NaN   

                                         
                            pga    rbch  
player         stat                      
Byeong Hun An  drv       306.50     NaN  
               gir        48.61     NaN  
               scramble   67.57     NaN  
Abraham Ancer  drv       301.80  299.90  
               gir        61.11   70.83  
...                         ...     ...  
Will Zalatoris gir        61.11   58.33  
               scramble   64.29   56.67  
Xinjun Zhang   drv          NaN     NaN  
               gir          NaN     NaN  
               scramble     NaN     NaN  

[678 rows x 9 columns]

In [30]:
# all that's left is to figure out how to use this data set in some meaningful fashion